In [485]:
import os
import random
import pickle
import zipfile
import numpy as np

#### Load HistWords dataset:

In [486]:
# # dataset obtained from here: https://github.com/williamleif/histwords

# # load dataset here:
# !git clone https://github.com/williamleif/histwords.git
# !wget -O all_english_embeddings.zip "http://snap.stanford.edu/historical_embeddings/eng-all_sgns.zip"

# # unzip loaded dataset
# with zipfile.ZipFile("all_english_embeddings.zip", 'r') as zip_ref:
#     zip_ref.extractall("all_english_embeddings")

## Step 1: Load and Preprocess Word Embeddings

In [487]:
# for loading historical embeddings from .npy files
def load_embeddings(file_path):
    return np.load(file_path)

In [488]:
# base dir for embeddings
base_dir = "all_english_embeddings/sgns"
print(os.getcwd()) # debugging

/Users/bryan/Documents/College/Computer Science/CMSC 491 - Modern Regression/Project/code


#### Obtain subsample of words from dataset:

In [489]:
# specify decades of interest
decades = ['1880', '1890', '1900', '1910', '1920', '1930', '1940', '1950', '1960', '1970', '1980']
vocab_dict = {}
embeddings_dict = {}
random.seed(69)         # set desired seed here
sample_size = 500       # set desired sample size here

In [490]:
# load and optionally sample each decade's embeddings and vocabulary
for decade in decades:
    # load embeddings
    embedding_path = os.path.join(base_dir, f"{decade}-w.npy")
    embeddings = load_embeddings(embedding_path)
    
    # load vocabulary
    vocab_path = os.path.join(base_dir, f"{decade}-vocab.pkl")
    with open(vocab_path, 'rb') as f:
        vocab = pickle.load(f)
    
    # ensure embeddings and vocab are same size
    assert len(embeddings) == len(vocab), f"Mismatch in size for {decade}"

    # filter out any numerical values counted as "words"
    filtered_vocab = []
    filtered_embeddings = []
    for word, embedding in zip(vocab, embeddings):
        if not any(char.isdigit() for char in word):
            filtered_vocab.append(word)
            filtered_embeddings.append(embedding)

    # fill dicts
    vocab_dict[decade] = filtered_vocab
    embeddings_dict[decade] = np.array(filtered_embeddings)

#### Filter subsamples by intersection across decades:

In [491]:
# obtain common vocabulary across all decades
common_vocab = set(vocab_dict[decades[0]])
for decade in decades[1:]:
    common_vocab.intersection_update(vocab_dict[decade])

common_vocab = list(common_vocab)  # converted to list for indexing

In [492]:
# precompute word_to_index dictionaries for each decade
word_to_index_dict = {}
for decade in decades:
    vocab = vocab_dict[decade]
    word_to_index = {word: idx for idx, word in enumerate(vocab)}
    word_to_index_dict[decade] = word_to_index

# rand sample from common_vocab
initial_sample_size = sample_size * 2  # increase here to account for possible zero vectors
sampled_words = random.sample(common_vocab, min(initial_sample_size, len(common_vocab)))

valid_words = []
zero_vector = np.zeros(embeddings_dict[decades[0]].shape[1])

for word in sampled_words:
    has_zero_vector = False
    for decade in decades:
        idx = word_to_index_dict[decade][word]
        embedding = embeddings_dict[decade][idx]
        if np.array_equal(embedding, zero_vector):
            has_zero_vector = True
            break
    if not has_zero_vector:
        valid_words.append(word)
    if len(valid_words) >= sample_size:
        break  # stop if we have enough valid words

print(f"Number of valid words (non-zero embeddings in all decades): {len(valid_words)}")

# update vocab_dict and embeddings_dict
for decade in decades:
    embeddings = embeddings_dict[decade]
    word_to_index = word_to_index_dict[decade]
    
    # obtain embeddings for valid_words
    indices = [word_to_index[word] for word in valid_words]
    filtered_embeddings = embeddings[indices]
    
    # update dicts with filtered values
    vocab_dict[decade] = valid_words
    embeddings_dict[decade] = filtered_embeddings


Number of valid words (non-zero embeddings in all decades): 281


In [493]:
# debugging
for decade, embeddings in embeddings_dict.items():
    print(f"{decade}'s embeddings:")
    print(f"shape: {embeddings.shape}") # display shape of embeddings per decade
    print(embeddings_dict[decade][:5])  # display first n rows of embeddings per decade
    print()

1880's embeddings:
shape: (281, 300)
[[-0.04577171  0.05883226 -0.00495697 ... -0.03815761 -0.06006648
  -0.03318118]
 [-0.09662315  0.00508403  0.03041487 ... -0.14422784 -0.09366461
  -0.03934779]
 [ 0.11799512 -0.01379209  0.03675429 ... -0.02668592  0.06114693
   0.03621142]
 [ 0.05996715  0.01390738 -0.06524581 ...  0.0483136   0.07105128
  -0.03990979]
 [ 0.01158068 -0.07635602  0.11213172 ... -0.08607953 -0.04759826
   0.00298743]]

1890's embeddings:
shape: (281, 300)
[[-0.01153982  0.01141271 -0.00083333 ... -0.08022841 -0.00839751
  -0.01876197]
 [-0.06090894  0.04529386 -0.03509929 ... -0.11167352 -0.06853096
   0.00019286]
 [ 0.11020987 -0.05960207  0.01661427 ... -0.08961481  0.08627959
   0.07659143]
 [-0.03292909 -0.03031674  0.00754662 ...  0.07281497  0.06993163
  -0.02926835]
 [ 0.01925231 -0.06563794  0.09719697 ... -0.09667907 -0.03455876
  -0.00361501]]

1900's embeddings:
shape: (281, 300)
[[-0.00824413 -0.01112733  0.00367004 ... -0.05263169 -0.01965667
   0.0188

## Step 2: Standardize Data

In [494]:
def standardize(data):
    """
    Manually standardizes data by centering (subtracting mean) and scaling (dividing by standard deviation).
    
    Parameters:
    data (numpy.ndarray): Input data matrix of shape (num_vectors, num_dimensions).
    
    Returns:
    standardized_data (numpy.ndarray): Standardized data with zero mean and unit variance.
    mean_vector (numpy.ndarray): Computed mean vector.
    std_vector (numpy.ndarray): Computed standard deviation vector.
    """
    num_vectors, num_dimensions = len(data), len(data[0])
    mean_vector = [0] * num_dimensions
    std_vector = [0] * num_dimensions
    
    # compute mean
    for vector in data:
        mean_vector += vector
    mean_vector /= num_vectors
    
    # compute standard deviation
    for vector in data:
        std_vector += (vector - mean_vector) ** 2
    std_vector = (std_vector / num_vectors) ** 0.5
    
    # avoid division by zero (s.t. if a dimension has zero variance, set std to 1)
    std_vector[std_vector == 0] = 1.0
    
    # center and scale data
    standardized_data = [0] * len(data)
    for i in range(num_vectors):
        standardized_data[i] = (data[i] - mean_vector) / std_vector
    
    return np.array(standardized_data), np.array(mean_vector), np.array(std_vector)

In [495]:
std_embeddings_dict = {}
for decade, embeddings in embeddings_dict.items():
    standardized_data, _, _ = standardize(embeddings_dict[decade])
    std_embeddings_dict[decade] = standardized_data

#### Before centering (values small, but not entirely close to zero):

In [496]:
# debugging
for decade, embeddings in embeddings_dict.items():
    _, mean_vector, _ = standardize(embeddings)
    print(f"Mean vector for non-centered embeddings ({decade}'s):")
    print(mean_vector[:5])
    print()

Mean vector for non-centered embeddings (1880's):
[ 0.01822707  0.03680266  0.00309692 -0.0058666  -0.00646067]

Mean vector for non-centered embeddings (1890's):
[ 0.02234161  0.0332645   0.00579541 -0.00114613 -0.01232974]

Mean vector for non-centered embeddings (1900's):
[ 0.01717167  0.03257055  0.0034977  -0.00329823 -0.00537224]

Mean vector for non-centered embeddings (1910's):
[ 0.02060214  0.03305729  0.0063528  -0.00524798 -0.00864907]

Mean vector for non-centered embeddings (1920's):
[ 0.02004428  0.03814782  0.01392256 -0.00400352 -0.01089536]

Mean vector for non-centered embeddings (1930's):
[ 0.02129032  0.03892836  0.00952735 -0.00815879 -0.0101349 ]

Mean vector for non-centered embeddings (1940's):
[ 0.02655882  0.0410243   0.00949306 -0.00902392 -0.00863616]

Mean vector for non-centered embeddings (1950's):
[ 0.03098091  0.04671023  0.00838624 -0.00961563 -0.01074204]

Mean vector for non-centered embeddings (1960's):
[ 0.02380229  0.04270789  0.01096229 -0.012492

#### After centering (values now much closer to zero):

In [497]:
# debugging
for decade, embeddings in std_embeddings_dict.items():
    _, mean_vector, _ = standardize(embeddings)
    print(f"Mean vector for centered embeddings ({decade}'s):")
    print(mean_vector[:5])
    print()

Mean vector for centered embeddings (1880's):
[ 2.32317131e-16  5.37332140e-17  2.15327953e-17  9.32429302e-17
 -2.41009269e-17]

Mean vector for centered embeddings (1890's):
[ 1.25245800e-16  2.97903260e-16 -4.50410764e-17 -2.68666070e-17
  1.18529149e-17]

Mean vector for centered embeddings (1900's):
[-3.27930644e-17 -3.14497341e-16 -2.92371900e-17  7.19076834e-17
  1.58038865e-18]

Mean vector for centered embeddings (1910's):
[-1.58038865e-16  1.36703618e-16 -6.16351572e-17  1.12207594e-16
  3.95097162e-19]

Mean vector for centered embeddings (1920's):
[-3.16077729e-17  1.20109537e-16 -7.26978778e-17  2.37058297e-18
  1.85893215e-16]

Mean vector for centered embeddings (1930's):
[ 2.14932856e-16 -3.42154142e-16  1.78979014e-16 -6.79567118e-17
  4.89920481e-17]

Mean vector for centered embeddings (1940's):
[-2.14142662e-16  8.77115699e-17  4.02999105e-17 -6.47959345e-17
 -6.32155459e-18]

Mean vector for centered embeddings (1950's):
[ 2.02289747e-16  2.67085681e-16  7.61549779

## Step 3: Compute Covariance Matrix (old)

In [498]:
# combine embeddings from all decades into one dataset for unified coordinate space
combined_embeddings = np.vstack([std_embeddings_dict[decade] for decade in decades])

In [499]:
def compute_cv_matrix(data):
    """
    Manually computes covariance matrix of input data.
    
    Parameters:
    data (numpy.ndarray): Centered data matrix of shape (num_vectors, num_dimensions).
    
    Returns:
    covariance_matrix (numpy.ndarray): Covariance matrix of shape (num_dimensions, num_dimensions).
    """
    data = np.array(data)
    num_vectors = data.shape[0] # init cv matrix
    covariance_matrix = (data.T @ data) / (num_vectors - 1) # cv cmoputed with matrix multiplication and element-wise averaging

    return covariance_matrix

In [500]:
# find cv matrix of combined embeddings
cv_matrix = compute_cv_matrix(combined_embeddings)

# the cv matrix should be symmetric (debugging)
print("Is symmetric? ", np.allclose(cv_matrix, cv_matrix.T)) # should print True if symmetric

Is symmetric?  True


## Step 4: Compute Eigenvalues/Eigenvectors of Covariance Matrix

In [501]:
def random_vector(size):
    """
    Generates a random vector of specified size using Python's random module.
    
    Parameters:
    size (int): Size of random vector.
    
    Returns:
    list: Random vector with values between 0 and 1.
    """
    return [random.random() for _ in range(size)]

In [502]:
def l2_norm(vector):
    """
    Manually computes Euclidean (L2) norm of vector.
    
    Parameters:
    vector (numpy.ndarray): Input vector.
    
    Returns:
    float: Euclidean norm of vector.
    """
    sum_of_squares = 0.0
    for value in vector:
        sum_of_squares += value ** 2
    return sum_of_squares ** 0.5

In [503]:
def power_iteration(matrix, num_iterations=1000, tolerance=1e-9):
    """
    Manually computes largest eigenvalue and its corresponding eigenvector using power iteration.
    
    Parameters:
    matrix (numpy.ndarray): Input square matrix.
    num_iterations (int): Number of iterations to perform.
    tolerance (float): Convergence tolerance.
    
    Returns:
    largest_eigenvalue (float): Largest eigenvalue.
    eigenvector (numpy.ndarray): Corresponding eigenvector.
    """
    # init random vector
    b_k = random_vector(matrix.shape[1])
    
    for _ in range(num_iterations):
        # matrix-vector multiplication
        b_k1 = (matrix @ b_k)

        # normalize vector
        b_k1_norm = l2_norm(b_k1)
        b_k1 = b_k1 / b_k1_norm
        
        # check convergence
        if l2_norm(b_k1 - b_k) < tolerance:
            break
        b_k = b_k1
    
    # compute corresponding eigenvalue
    largest_eigenvalue = (b_k.T @ (matrix @ b_k)) / (b_k.T @ b_k)
    
    return largest_eigenvalue, b_k

In [504]:
# debugging
largest_eigenvalue, eigenvector = power_iteration(cv_matrix)
print("Largest Eigenvalue:", largest_eigenvalue)

Largest Eigenvalue: 9.893102524924167


## Step 5: Select Largest k Eigenvalues

In [505]:
def largest_k_eigenvalues(matrix, k, num_iterations=1000, tolerance=1e-9):
    """
    Computes largest k eigenvalues and their corresponding eigenvectors using power iteration and deflation.
    
    Parameters:
    matrix (numpy.ndarray): Input square matrix.
    k (int): Number of top eigenvalues/eigenvectors to find.
    num_iterations (int): Number of iterations for each power iteration step.
    tolerance (float): Convergence tolerance for power iteration.
    
    Returns:
    eigenvalues (list): List of top k eigenvalues.
    eigenvectors (list): List of corresponding eigenvectors.
    """
    matrix_copy = matrix[:] # copy of matrix to avoid modifying original
    eigenvalues = []
    eigenvectors = []

    for _ in range(k):
        # find largest eigenvalue and corresponding eigenvector
        largest_eigenvalue, eigenvector = power_iteration(matrix_copy, num_iterations, tolerance)
        eigenvalues.append(largest_eigenvalue)
        eigenvectors.append(eigenvector)

        # deflation step, remove component corresponding to found eigenvector
        matrix_copy = matrix_copy - largest_eigenvalue * np.outer(eigenvector, eigenvector)

    return eigenvalues, np.array(eigenvectors)

In [506]:
# debugging
k = 3
eigenvalues, eigenvectors = largest_k_eigenvalues(cv_matrix, k)
print(f"Largest k = {k} eigenvalues:", eigenvalues)

Largest k = 3 eigenvalues: [9.893102524924169, 8.306778156675488, 6.42338321093667]


## Step 6: Project Data Onto New Space

In [507]:
def transpose(matrix):
    """
    Manually transposes a given matrix.
    
    Parameters:
    matrix (list of lists): Input matrix for transposition.
    
    Returns:
    transposed (list of lists): Transposed matrix.
    """
    return [[row[i] for row in matrix] for i in range(len(matrix[0]))]

In [508]:
# project each decade's embeddings onto common basis
proj_embeddings_dict = {}
for decade in decades:
    projected_embeddings = (std_embeddings_dict[decade] @ transpose(eigenvectors)) # transpose eigenvectors here
    proj_embeddings_dict[decade] = projected_embeddings

In [509]:
print("Keys in transf_embeddings_dict:", proj_embeddings_dict.keys())

Keys in transf_embeddings_dict: dict_keys(['1880', '1890', '1900', '1910', '1920', '1930', '1940', '1950', '1960', '1970', '1980'])


## Step 7: Plot Resulting Data in Reduced Domain

In [510]:
import plotly.graph_objs as go
import plotly.offline as py

In [511]:
def interpolate_points(data1, data2, num_interpolations=10):
    """Interpolates between two sets of points."""
    interpolated_data = []
    for alpha in np.linspace(0, 1, num_interpolations):
        interpolated = (1 - alpha) * data1 + alpha * data2
        interpolated_data.append(interpolated)
    return interpolated_data

In [512]:
frames = []
text_size = 8
marker_size = 3
num_interpolations = 20  # adjust for smoother transitions here

for i in range(len(decades) - 1):
    curr_decade = decades[i]
    next_decade = decades[i + 1]
    curr_data = proj_embeddings_dict[curr_decade]
    next_data = proj_embeddings_dict[next_decade]
    
    # create interpolated frames
    interpolated_frames = interpolate_points(curr_data, next_data, num_interpolations)
    
    for j, interpolated_data in enumerate(interpolated_frames):
        frame = go.Frame(
            data=[
                go.Scatter3d(
                    x=interpolated_data[:, 0],
                    y=interpolated_data[:, 1],
                    z=interpolated_data[:, 2],
                    mode='markers+text',
                    marker=dict(size=marker_size, color='blue'),
                    text=vocab_dict[curr_decade],
                    textfont=dict(size=text_size),
                    name=f"Interpolation {i}-{j}"
                )
            ],
            name=f"Frame {i}-{j}",
        )
        frames.append(frame)

frames.append(
    go.Frame(
        data=[
            go.Scatter3d(
                x=proj_embeddings_dict[decades[-1]][:, 0],
                y=proj_embeddings_dict[decades[-1]][:, 1],
                z=proj_embeddings_dict[decades[-1]][:, 2],
                mode='markers+text',
                marker=dict(size=marker_size, color='blue'),
                text=vocab_dict[decades[-1]],
                name=decades[-1]
            )
        ],
        name=f"Frame {len(decades) - 1}-0"
    )
)

In [513]:
# fixed axis ranges
axes_bounds = 10
x_min, x_max = -axes_bounds, axes_bounds
y_min, y_max = -axes_bounds, axes_bounds
z_min, z_max = -axes_bounds, axes_bounds

axes_intervals = [x_min, -axes_bounds/2, 0, axes_bounds/2, x_max]

layout = go.Layout(
    title="3D Visualization of Word Embeddings Over Time",
    margin=dict(l=0, r=0, b=0, t=40),
    scene=dict(
        xaxis=dict(title="PC1", range=[x_min, x_max], tickvals=axes_intervals, autorange=False),
        yaxis=dict(title="PC2", range=[y_min, y_max], tickvals=axes_intervals, autorange=False),
        zaxis=dict(title="PC3", range=[z_min, z_max], tickvals=axes_intervals, autorange=False),
        aspectmode='manual',
        aspectratio=dict(x=1, y=1, z=1),
    ),
    height=800,
    sliders=[{
        "steps": [
            {
                "args": [[f"Frame {i}-0"], {
                    "frame": {"duration": 100, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 100}
                }],
                "label": f"{decades[i]}",
                "method": "animate"
            }
            for i in range(len(decades))
        ],
        "active": 0,
        "x": 0.2,
        "xanchor": "left",
        "y": 0,
        "yanchor": "top",
        "len": 0.5
    }],
    updatemenus=[{
        "buttons": [
            {
                "args": [None, {
                    "frame": {"duration": 100, "redraw": True},
                    "mode": "immediate",
                    "fromcurrent": True
                }],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[None], {
                    "frame": {"duration": 0, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 0}
                }],
                "label": "Pause",
                "method": "animate"
            },
            {
                "args": [[f"Frame 0-0"], {  # reset to first interpolated frame
                    "frame": {"duration": 0, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 0}
                }],
                "label": "Reset",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }]
)

fig = go.Figure(data=[frames[0].data[0]], layout=layout, frames=frames)
py.iplot(fig)

## Step 8: Quantify Semantic Volatility of Select Words

In [514]:
# calculate shifts for all words across decades
def calculate_shift_magnitudes(embeddings, vocab_dict):
    shift_magnitudes = {}  # dict to store word-shift pairs

    # sort decades for consistency
    decades = sorted(embeddings.keys())

    # traverse all words in vocab dict
    for word in vocab_dict[decades[0]]:  # vocab should be same for all decades given preprocessing step
        word_shifts = []

        # traverse through consecutive decades to calculate shifts for each word
        for i in range(len(decades) - 1):
            curr_decade, next_decade = decades[i], decades[i + 1]

            # check if word exists in both curr and next decades
            if word in vocab_dict[curr_decade] and word in vocab_dict[next_decade]:
                # index of word in each decade's vocabulary
                index_curr = vocab_dict[curr_decade].index(word)
                index_next = vocab_dict[next_decade].index(word)

                # embeddings for word in curr and next decade
                curr_embedding = embeddings[curr_decade][index_curr]
                next_embedding = embeddings[next_decade][index_next]

                # find delta (change in coordinates)
                delta = next_embedding - curr_embedding

                # calculate Euclidean norm (magnitude of shift)
                shift_magnitude = l2_norm(delta)

                # add shift magnitude to list for targeted word
                word_shifts.append(shift_magnitude)

        # add word and its corresponding shift magnitudes to dict
        shift_magnitudes[word] = word_shifts

    return shift_magnitudes


In [515]:
# calculate shift magnitudes for each word
volatility_scores = calculate_shift_magnitudes(proj_embeddings_dict, vocab_dict)

# dict for overall volatility score for each word
overall_volatility_scores = {}

# calculate an overall volatility score for each word (std dev)
for word, shifts in volatility_scores.items():
    if len(shifts) > 0:  # consider words with at least one shift value
        # other options here include using: np.sum(shifts), np.mean(shifts), or np.std(shifts) to quantify volatility
        overall_volatility_scores[word] = np.std(shifts)

# sort words by overall volatility score in descending order
sorted_volatility = sorted(overall_volatility_scores.items(), key=lambda x: x[1], reverse=True)

# output top N most volatile words
N = 300
for word, score in sorted_volatility[:N]:
    print(f"Volatility score for '{word}': {score}")


Volatility score for 'jerry': 1.4391087264194797
Volatility score for 'lancelot': 1.2836213515935018
Volatility score for 'saturate': 1.0798590012228975
Volatility score for 'tristan': 1.0687743790309998
Volatility score for 'myers': 0.9529892962367498
Volatility score for 'freest': 0.8599716533693398
Volatility score for 'vas': 0.8299200643368339
Volatility score for 'muir': 0.8261277614587563
Volatility score for 'granaries': 0.8153089106440999
Volatility score for 'lyttelton': 0.812925686934777
Volatility score for 'exposures': 0.792197229484528
Volatility score for 'delphi': 0.7353617671128394
Volatility score for 'sprague': 0.7299266975114258
Volatility score for 'clog': 0.7013251875649633
Volatility score for 'scrip': 0.7010428325332961
Volatility score for 'distrusted': 0.691421975980068
Volatility score for 'bowen': 0.6906403628538687
Volatility score for 'irene': 0.6832725285914776
Volatility score for 'smithsonian': 0.6822577040802389
Volatility score for 'burgoyne': 0.680202